In [1]:
#Install necessary libraries

import numpy as np
import pandas as pd
import requests
# KO : pip install folium
# KO : conda install -c conda-forge folium
# KO : python3 -m pip install folium
!pip install folium
import folium
import matplotlib.cm as cm
import matplotlib.colors as colors
import json
from sklearn.cluster import KMeans

#import geopy
#from geopy.geocoders import Nominatim
from pandas.io.json import json_normalize

# add bs4 library:
from bs4 import BeautifulSoup
import lxml

import types

print('Libraries imported.')

Libraries imported.


In [6]:
myCP=pd.read_csv('angers_laposte_hexasmal.csv',delimiter=';')
myCP.head()

Code_INSEE  Nom_commune        lat      long
0       49007       ANGERS  47.476837 -0.556126
1       49015      AVRILLE  47.505711 -0.600789
2       49020    BEAUCOUZE  47.474451 -0.634055
3       49028      BEHUARD  47.376691 -0.653916
4       49035  BOUCHEMAINE  47.430767 -0.627122

In [94]:
# create the map of Angers with the postal codes :
import folium
map_angers = folium.Map(location=[47.478419, -0.563166], zoom_start=11)
for lat, lng, Code_INSEE, Nom_commune in zip(
        myCP['lat'], 
        myCP['long'], 
        myCP['Code_INSEE'], 
        myCP['Nom_commune']):
    label = '{}, {}'.format(Code_INSEE, Nom_commune)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='black',
        fill=True,
        fill_color='#000000',
        fill_opacity=0.7,
        parse_html=False).add_to(map_angers)  

map_angers


In [7]:
my_equip_49=pd.read_csv('234400034_004-009_activites-des-fiches-equipements-rpdl_CL_49.csv',delimiter=';')
my_equip_49_foot=pd.read_csv('234400034_004-009_activites-des-fiches-equipements-rpdl_CL_49.csv',delimiter=';')
my_equip_49_basket=pd.read_csv('234400034_004-009_activites-des-fiches-equipements-rpdl_CL_49.csv',delimiter=';')
my_equip_49_swim=pd.read_csv('234400034_004-009_activites-des-fiches-equipements-rpdl_CL_49.csv',delimiter=';')
del my_equip_49_foot['Departement']
del my_equip_49_foot['Numero_fiche_equipement']
del my_equip_49_foot['code_region']
del my_equip_49_foot['Libelle_departement']
del my_equip_49_foot['Activite_praticable']
del my_equip_49_foot['Activite_pratiquee']
del my_equip_49_foot['Salle_specialisable']
del my_equip_49_foot['Activite code']
del my_equip_49_basket['Departement']
del my_equip_49_basket['Numero_fiche_equipement']
del my_equip_49_basket['code_region']
del my_equip_49_basket['Libelle_departement']
del my_equip_49_basket['Activite_praticable']
del my_equip_49_basket['Activite_pratiquee']
del my_equip_49_basket['Salle_specialisable']
del my_equip_49_basket['Activite code']
del my_equip_49_swim['Departement']
del my_equip_49_swim['Numero_fiche_equipement']
del my_equip_49_swim['code_region']
del my_equip_49_swim['Libelle_departement']
del my_equip_49_swim['Activite_praticable']
del my_equip_49_swim['Activite_pratiquee']
del my_equip_49_swim['Salle_specialisable']
del my_equip_49_swim['Activite code']
my_equip_49.head()

Activite_libelle  Departement Libelle_departement  Code_INSEE Nom_commune  \
0      Basket-Ball           49      Maine-et-Loire       49007      Angers   
1      Basket-Ball           49      Maine-et-Loire       49007      Angers   
2      Basket-Ball           49      Maine-et-Loire       49007      Angers   
3      Basket-Ball           49      Maine-et-Loire       49007      Angers   
4      Basket-Ball           49      Maine-et-Loire       49007      Angers   

   Numero_fiche_equipement  Nombre_equipements  Activite code  \
0                    67299                   1           1101   
1                    67521                   2           1101   
2                    69177                   1           1101   
3                    69950                   1           1101   
4                    69966                   2           1101   

  Activite_libelle.1 Activite_praticable Activite_pratiquee  \
0        Basket-Ball                 Oui                Oui   
1        Basket-Ball                 Oui                Oui   
2        Basket-Ball                 Oui                Oui   
3        Basket-Ball                 Oui                Oui   
4        Basket-Ball                 Oui                Oui   

  Salle_specialisable Niveau_activite        lat      long  code_region  
0                 Non             NaN  47.476837 -0.556126           52  
1                 Non             NaN  47.476837 -0.556126           52  
2                 Non             NaN  47.476837 -0.556126           52  
3                 Non             NaN  47.476837 -0.556126           52  
4                 Non        Scolaire  47.476837 -0.556126           52

In [8]:
#Foot equipments data input
my_equip_49_foot['foot_bool'] = np.where(my_equip_49_foot['Activite_libelle']=="Football / Football en salle (Futsal)", 'oui', 'non')
# Get names of indexes for which column foot_bool has value non
indexNames = my_equip_49_foot[ my_equip_49_foot['foot_bool'] == 'non' ].index
# Delete these row indexes from dataFrame
my_equip_49_foot.drop(indexNames , inplace=True)
my_equip_49_foot.join (myCP.set_index( [ 'Code_INSEE' ], verify_integrity=True ), on=[ 'Code_INSEE' ], how='left' , lsuffix='_left', rsuffix='_right')
my_equip_49_foot.head()

Activite_libelle  Code_INSEE Nom_commune  \
764  Football / Football en salle (Futsal)       49007      Angers   
765  Football / Football en salle (Futsal)       49007      Angers   
766  Football / Football en salle (Futsal)       49007      Angers   
767  Football / Football en salle (Futsal)       49007      Angers   
768  Football / Football en salle (Futsal)       49007      Angers   

     Nombre_equipements                     Activite_libelle.1  \
764                   1  Football / Football en salle (Futsal)   
765                   1  Football / Football en salle (Futsal)   
766                   1  Football / Football en salle (Futsal)   
767                   1  Football / Football en salle (Futsal)   
768                   1  Football / Football en salle (Futsal)   

    Niveau_activite        lat      long foot_bool  
764    Entrainement  47.476837 -0.556126       oui  
765             NaN  47.476837 -0.556126       oui  
766        Scolaire  47.476837 -0.556126       oui  
767             NaN  47.476837 -0.556126       oui  
768             NaN  47.476837 -0.556126       oui

In [87]:
# create the map of Nantes with the football equipments :
import folium
map_angers_foot = folium.Map(location=[47.478419, -0.563166], zoom_start=10)
for lat, lng, Code_INSEE, Nom_commune in zip(
        my_equip_49_foot['lat'], 
        my_equip_49_foot['long'], 
        my_equip_49_foot['Code_INSEE'], 
        my_equip_49_foot['Nom_commune'] ):
    label = '{}, {}'.format(Code_INSEE, Nom_commune)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='green',
        fill=True,
        fill_color='#008000',
        fill_opacity=0.7,
        parse_html=False).add_to(map_angers_foot)  

map_angers_foot

In [9]:
#Basket equipments data input
my_equip_49_basket['basket_bool'] = np.where(my_equip_49_basket['Activite_libelle']=="Basket-Ball", 'oui', 'non')
# Get names of indexes for which column basket_bool has value non
indexNames = my_equip_49_basket[ my_equip_49_basket['basket_bool'] == 'non' ].index
# Delete these row indexes from dataFrame
my_equip_49_basket.drop(indexNames , inplace=True)
my_equip_49_basket.join (myCP.set_index( [ 'Code_INSEE' ], verify_integrity=True ), on=[ 'Code_INSEE' ], how='left' , lsuffix='_left', rsuffix='_right')
my_equip_49_basket.head()

Activite_libelle  Code_INSEE Nom_commune  Nombre_equipements  \
0      Basket-Ball       49007      Angers                   1   
1      Basket-Ball       49007      Angers                   2   
2      Basket-Ball       49007      Angers                   1   
3      Basket-Ball       49007      Angers                   1   
4      Basket-Ball       49007      Angers                   2   

  Activite_libelle.1 Niveau_activite        lat      long basket_bool  
0        Basket-Ball             NaN  47.476837 -0.556126         oui  
1        Basket-Ball             NaN  47.476837 -0.556126         oui  
2        Basket-Ball             NaN  47.476837 -0.556126         oui  
3        Basket-Ball             NaN  47.476837 -0.556126         oui  
4        Basket-Ball        Scolaire  47.476837 -0.556126         oui

In [88]:
# create the map of Nantes with the basket equipments :
import folium
map_angers_basket = folium.Map(location=[47.478419, -0.563166], zoom_start=10)
for lat, lng, Code_INSEE, Nom_commune in zip(
        my_equip_49_basket['lat'], 
        my_equip_49_basket['long'], 
        my_equip_49_basket['Code_INSEE'], 
        my_equip_49_basket['Nom_commune']):
    label = '{}, {}'.format(Code_INSEE, Nom_commune)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='red',
        fill=True,
        fill_color='#FF0000',
        fill_opacity=0.7,
        parse_html=False).add_to(map_angers_basket)  

map_angers_basket

In [10]:
#Swimming pools equipments data input
my_equip_49_swim['swim_bool'] = np.where(my_equip_49_swim['Activite_libelle']=="Natation course sportive", 'oui', 'non')
# Get names of indexes for which column swim_bool has value non
indexNames = my_equip_49_swim[ my_equip_49_swim['swim_bool'] == 'non' ].index
# Delete these row indexes from dataFrame
my_equip_49_swim.drop(indexNames , inplace=True)
my_equip_49_swim.join (myCP.set_index( [ 'Code_INSEE' ], verify_integrity=True ), on=[ 'Code_INSEE' ], how='left' , lsuffix='_left', rsuffix='_right')
my_equip_49_swim.head()

Activite_libelle  Code_INSEE       Nom_commune  \
1851  Natation course sportive       49125  Doue-la-Fontaine   
1852  Natation course sportive       49127            Durtal   
1853  Natation course sportive       49328            Saumur   
1854  Natation course sportive       49007            Angers   
1855  Natation course sportive       49007            Angers   

      Nombre_equipements        Activite_libelle.1 Niveau_activite        lat  \
1851                   1  Natation course sportive    Entrainement  47.191472   
1852                   1  Natation course sportive    Entrainement  47.678052   
1853                   1  Natation course sportive    Entrainement  47.267385   
1854                   1  Natation course sportive             NaN  47.476837   
1855                   1  Natation course sportive             NaN  47.476837   

          long swim_bool  
1851 -0.278336       oui  
1852 -0.254608       oui  
1853 -0.083041       oui  
1854 -0.556126       oui  
1855 -0.556126       oui

In [86]:
# create the map of Nantes with the swim equipments :
import folium
map_angers_swim = folium.Map(location=[47.478419, -0.563166], zoom_start=10)
for lat, lng, Code_INSEE, Nom_commune in zip(
        my_equip_49_swim['lat'], 
        my_equip_49_swim['long'], 
        my_equip_49_swim['Code_INSEE'], 
        my_equip_49_swim['Nom_commune']):
    label = '{}, {}'.format(Code_INSEE, Nom_commune)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#0000FF',
        fill_opacity=0.7,
        parse_html=False).add_to(map_angers_swim)  

map_angers_swim

In [1]:
#Basical_statistics of equipments numbers by level of activities
#Foot
my_stat_level_foot=my_equip_49_foot[["Code_INSEE","Niveau_activite", "Nombre_equipements"]]
my_stat_level_foot2=my_equip_49_foot[["Code_INSEE","Niveau_activite", "Nombre_equipements"]]

#my_stat_level_foot.shape
my_stat_level_foot2["Nombre_equipements"].apply(pd.to_numeric)
my_stat_level_foot2=my_stat_level_foot.groupby(by=["Code_INSEE","Niveau_activite"]).sum().reset_index()

my_stat_level_foot2.loc[my_stat_level_foot2["Niveau_activite"] == "Competition departementale","Niveau_activite"] = "Competition"
my_stat_level_foot2.loc[my_stat_level_foot2["Niveau_activite"] == "Competition regionale","Niveau_activite"] = "Competition"
my_stat_level_foot2.loc[my_stat_level_foot2["Niveau_activite"] == "Competition nationale","Niveau_activite"] = "Competition"
my_stat_level_foot2.loc[my_stat_level_foot2["Niveau_activite"] == "Competition internationale","Niveau_activite"] = "Competition"
my_stat_level_foot2.loc[my_stat_level_foot2["Niveau_activite"] == "Entrainement","Niveau_activite"] = "Training"
my_stat_level_foot2.loc[my_stat_level_foot2["Niveau_activite"] == "Loisir - Entretien - Remise en forme","Niveau_activite"] = "Leisure"

my_stat_level_foot2

NameError: name 'my_equip_49_foot' is not defined

In [94]:
#Basical_statistics of equipments numbers by level of activities
#Basket
my_stat_level_basket=my_equip_49_basket[["Code_INSEE","Niveau_activite", "Nombre_equipements"]]
my_stat_level_basket2=my_equip_49_basket[["Code_INSEE","Niveau_activite", "Nombre_equipements"]]

# my_stat_level_basket.shape
my_stat_level_basket2["Nombre_equipements"].apply(pd.to_numeric)
my_stat_level_basket2=my_stat_level_basket.groupby(by=["Code_INSEE","Niveau_activite"]).sum().reset_index()

my_stat_level_basket2.loc[my_stat_level_basket2["Niveau_activite"] == "Competition departementale","Niveau_activite"] = "Competition"
my_stat_level_basket2.loc[my_stat_level_basket2["Niveau_activite"] == "Competition regionale","Niveau_activite"] = "Competition"
my_stat_level_basket2.loc[my_stat_level_basket2["Niveau_activite"] == "Competition nationale","Niveau_activite"] = "Competition"
my_stat_level_basket2.loc[my_stat_level_basket2["Niveau_activite"] == "Competition internationale","Niveau_activite"] = "Competition"
my_stat_level_basket2.loc[my_stat_level_basket2["Niveau_activite"] == "Entrainement","Niveau_activite"] = "Training"
my_stat_level_basket2.loc[my_stat_level_basket2["Niveau_activite"] == "Loisir - Entretien - Remise en forme","Niveau_activite"] = "Leisure"

my_stat_level_basket2

Code_INSEE Niveau_activite  Nombre_equipements
0         49002     Competition                   1
1         49003         Leisure                   1
2         49004         Leisure                   2
3         49006     Competition                   1
4         49007     Competition                   1
..          ...             ...                 ...
413       49373         Leisure                   1
414       49373        Scolaire                   1
415       49375     Competition                   1
416       49377     Competition                   1
417       49378        Scolaire                   1

[418 rows x 3 columns]

In [122]:
#Basical_statistics of equipments numbers by level of activities
#swim
my_stat_level_swim=my_equip_49_swim[["Code_INSEE","Niveau_activite", "Nombre_equipements"]]
my_stat_level_swim2=my_equip_49_swim[["Code_INSEE","Niveau_activite", "Nombre_equipements"]]

#my_stat_level_swim.shape
#(40, 3)

pd.to_numeric(my_stat_level_swim2.Nombre_equipements, downcast='integer')
my_stat_level_swim2=my_stat_level_swim.groupby(by=["Code_INSEE","Niveau_activite"]).sum().reset_index()

my_stat_level_swim2.shape
#(27, 3)

my_stat_level_swim2.loc[my_stat_level_swim2["Niveau_activite"] == "Competition departementale","Niveau_activite"] = "Competition"
my_stat_level_swim2.loc[my_stat_level_swim2["Niveau_activite"] == "Competition regionale","Niveau_activite"] = "Competition"
my_stat_level_swim2.loc[my_stat_level_swim2["Niveau_activite"] == "Competition nationale","Niveau_activite"] = "Competition"
my_stat_level_swim2.loc[my_stat_level_swim2["Niveau_activite"] == "Competition internationale","Niveau_activite"] = "Competition"
my_stat_level_swim2.loc[my_stat_level_swim2["Niveau_activite"] == "Entrainement","Niveau_activite"] = "Training"
my_stat_level_swim2.loc[my_stat_level_swim2["Niveau_activite"] == "Loisir - Entretien - Remise en forme","Niveau_activite"] = "Leisure"

my_stat_level_swim2

Code_INSEE Niveau_activite  Nombre_equipements
0        49007        Training                   1
1        49007        Scolaire                   1
2        49015     Competition                   1
3        49018        Training                   1
4        49041        Training                   1
5        49050        Training                   1
6        49054        Training                   1
7        49063        Training                   1
8        49080        Training                   1
9        49099     Competition                   1
10       49099         Leisure                   1
11       49103        Training                   1
12       49125        Training                   1
13       49127        Training                   1
14       49176        Training                   1
15       49180     Competition                   1
16       49180        Training                   1
17       49212        Training                   1
18       49228        Training                   1
19       49244        Training                   1
20       49259        Training                   2
21       49261        Training                   1
22       49267        Training                   2
23       49277        Training                   1
24       49328        Training                   4
25       49353        Training                   1
26       49367     Competition                   1

In [135]:
my_stat_level_foot3=my_stat_level_foot.groupby(by=["Nombre_equipements","Niveau_activite"]).agg(['count']).reset_index()

pd.to_numeric(my_stat_level_foot3.Nombre_equipements, downcast='integer')

my_stat_level_foot3

Nombre_equipements                       Niveau_activite Code_INSEE
                                                                 count
0                   1            Competition departementale        414
1                   1                 Competition nationale          1
2                   1                 Competition regionale         52
3                   1                          Entrainement        111
4                   1  Loisir - Entretien - Remise en forme        222
5                   1                            Non defini          1
6                   1                              Scolaire        156
7                   2            Competition departementale          6
8                   2                 Competition nationale          1
9                   2                 Competition regionale          2
10                  2                          Entrainement          4
11                  2  Loisir - Entretien - Remise en forme          5
12                  2                              Scolaire          7
13                  3            Competition departementale          1
14                  3                 Competition regionale          1
15                  3                          Entrainement          1
16                  3                              Scolaire          1
17                  4  Loisir - Entretien - Remise en forme          1

In [133]:
pd.to_numeric(my_stat_level_basket.Nombre_equipements, downcast='integer')

my_stat_level_basket3=my_stat_level_basket.groupby(by=["Nombre_equipements","Niveau_activite"]).agg(['count']).reset_index()

my_stat_level_basket3

Nombre_equipements                       Niveau_activite Code_INSEE
                                                                 count
0                   1            Competition departementale        169
1                   1            Competition internationale          2
2                   1                 Competition nationale          4
3                   1                 Competition regionale         24
4                   1                          Entrainement          6
5                   1  Loisir - Entretien - Remise en forme        223
6                   1                            Non defini          2
7                   1                              Scolaire        233
8                   2            Competition departementale          1
9                   2  Loisir - Entretien - Remise en forme         13
10                  2                              Scolaire         13
11                  3                              Scolaire          4
12                  4  Loisir - Entretien - Remise en forme          1
13                  4                              Scolaire          3

In [138]:
my_stat_level_swim3=my_stat_level_swim.groupby(by=["Nombre_equipements","Niveau_activite"]).agg(['count']).reset_index()

pd.to_numeric(my_stat_level_swim3.Nombre_equipements, downcast='integer')

my_stat_level_swim3

Nombre_equipements                       Niveau_activite Code_INSEE
                                                                count
0                  1            Competition departementale          1
1                  1                 Competition nationale          1
2                  1                 Competition regionale          2
3                  1                          Entrainement         26
4                  1  Loisir - Entretien - Remise en forme          1
5                  1                              Scolaire          1

In [140]:
# FOOT : CLUSTERING PREPARATION
pre_clustering_49_foot = my_equip_49_foot[["Code_INSEE","lat","long","Niveau_activite",'Nombre_equipements']]
#pre_clustering_49_foot.shape
#(855,5)
pre_clustering_49_foot.loc[pre_clustering_49_foot["Niveau_activite"] == "Competition departementale","Niveau_activite"] = "foot_Competition"
pre_clustering_49_foot.loc[pre_clustering_49_foot["Niveau_activite"] == "Competition regionale","Niveau_activite"] = "foot_Competition"
pre_clustering_49_foot.loc[pre_clustering_49_foot["Niveau_activite"] == "Competition nationale","Niveau_activite"] = "foot_Competition"
pre_clustering_49_foot.loc[pre_clustering_49_foot["Niveau_activite"] == "Competition internationale","Niveau_activite"] = "foot_Competition"
pre_clustering_49_foot.loc[pre_clustering_49_foot["Niveau_activite"] == "Entrainement","Niveau_activite"] = "foot_Training"
pre_clustering_49_foot.loc[pre_clustering_49_foot["Niveau_activite"] == "Loisir - Entretien - Remise en forme","Niveau_activite"] = "foot_Leisure"
#729 rows × 5 columns

grouped_clustering_49_foot = pre_clustering_49_foot.groupby(["Code_INSEE","lat","long","Niveau_activite"])['Nombre_equipements'].sum().reset_index(name="sum_nb_equip")
grouped_clustering_49_foot
#grouped_clustering_49_foot.shape
#(392,)

C:\ProgramData\Anaconda3\lib\site-packages\pandas\core\indexing.py:1765: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  isetter(loc, value)


Code_INSEE        lat      long   Niveau_activite  sum_nb_equip
0         49001  47.314889 -0.416673  foot_Competition             1
1         49001  47.314889 -0.416673     foot_Training             1
2         49002  47.303475  0.011113  foot_Competition             3
3         49003  47.257383 -0.337428  foot_Competition             2
4         49004  47.481702 -0.390970  foot_Competition             1
..          ...        ...       ...               ...           ...
496       49377  47.548654 -0.446940  foot_Competition             2
497       49377  47.548654 -0.446940     foot_Training             1
498       49378  47.322821 -0.066961  foot_Competition             1
499       49378  47.322821 -0.066961     foot_Training             1
500       49381  47.034497 -0.696856  foot_Competition             1

[501 rows x 5 columns]

In [141]:
# BASKET : CLUSTERING PREPARATION
pre_clustering_49_basket = my_equip_49_basket[["Code_INSEE","lat","long","Niveau_activite",'Nombre_equipements']]
# pre_clustering_49_basket=pre_clustering_49_basket.groupby(['Nombre_equipements']).min() : NO
pre_clustering_49_basket.loc[pre_clustering_49_basket["Niveau_activite"] == "Competition departementale","Niveau_activite"] = "basket_Competition"
pre_clustering_49_basket.loc[pre_clustering_49_basket["Niveau_activite"] == "Competition regionale","Niveau_activite"] = "basket_Competition"
pre_clustering_49_basket.loc[pre_clustering_49_basket["Niveau_activite"] == "Competition nationale","Niveau_activite"] = "basket_Competition"
pre_clustering_49_basket.loc[pre_clustering_49_basket["Niveau_activite"] == "Competition internationale","Niveau_activite"] = "basket_Competition"
pre_clustering_49_basket.loc[pre_clustering_49_basket["Niveau_activite"] == "Entrainement","Niveau_activite"] = "basket_Training"
pre_clustering_49_basket.loc[pre_clustering_49_basket["Niveau_activite"] == "Loisir - Entretien - Remise en forme","Niveau_activite"] = "basket_Leisure"
#2919 rows × 5 columns

grouped_clustering_49_basket = pre_clustering_49_basket.groupby(["Code_INSEE","lat","long","Niveau_activite"])['Nombre_equipements'].sum().reset_index(name="sum_nb_equip")
grouped_clustering_49_basket
#grouped_clustering_49_basket.shape
#(609,)


C:\ProgramData\Anaconda3\lib\site-packages\pandas\core\indexing.py:1765: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  isetter(loc, value)


Code_INSEE        lat      long     Niveau_activite  sum_nb_equip
0         49002  47.303475  0.011113  basket_Competition             1
1         49003  47.257383 -0.337428      basket_Leisure             1
2         49004  47.481702 -0.390970      basket_Leisure             2
3         49006  47.168615 -0.961142  basket_Competition             1
4         49007  47.476837 -0.556126          Non defini             1
..          ...        ...       ...                 ...           ...
404       49373  47.137330 -0.559450            Scolaire             1
405       49373  47.137330 -0.559450      basket_Leisure             1
406       49375  47.162328 -1.055389  basket_Competition             1
407       49377  47.548654 -0.446940  basket_Competition             1
408       49378  47.322821 -0.066961            Scolaire             1

[409 rows x 5 columns]

In [142]:
pre_clustering_49_swim = my_equip_49_swim[["Code_INSEE","lat","long","Niveau_activite",'Nombre_equipements']]
#del pre_clustering_49_swim['Nombre_equipements']
pre_clustering_49_swim.loc[pre_clustering_49_swim["Niveau_activite"] == "Competition departementale","Niveau_activite"] = "swim_Competition"
pre_clustering_49_swim.loc[pre_clustering_49_swim["Niveau_activite"] == "Competition regionale","Niveau_activite"] = "swim_Competition"
pre_clustering_49_swim.loc[pre_clustering_49_swim["Niveau_activite"] == "Competition nationale","Niveau_activite"] = "swim_Competition"
pre_clustering_49_swim.loc[pre_clustering_49_swim["Niveau_activite"] == "Competition internationale","Niveau_activite"] = "swim_Competition"
pre_clustering_49_swim.loc[pre_clustering_49_swim["Niveau_activite"] == "Entrainement","Niveau_activite"] = "swim_Training"
pre_clustering_49_swim.loc[pre_clustering_49_swim["Niveau_activite"] == "Loisir - Entretien - Remise en forme","Niveau_activite"] = "swim_Leisure"
#41 rows × 5 columns

grouped_clustering_49_swim = pre_clustering_49_swim.groupby(["Code_INSEE","lat","long","Niveau_activite"])['Nombre_equipements'].sum().reset_index(name="sum_nb_equip")
# no : grouped_clustering_49_swim.reset_index().rename(columns={'Nombre_equipements','SNE'})

grouped_clustering_49_swim
#grouped_clustering_49_swim.shape
#(33,)

C:\ProgramData\Anaconda3\lib\site-packages\pandas\core\indexing.py:1765: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  isetter(loc, value)


Code_INSEE        lat      long   Niveau_activite  sum_nb_equip
0        49007  47.476837 -0.556126          Scolaire             1
1        49007  47.476837 -0.556126     swim_Training             1
2        49015  47.505711 -0.600789  swim_Competition             1
3        49018  47.546689 -0.109022     swim_Training             1
4        49041  47.305692  0.071055     swim_Training             1
5        49050  47.341668 -0.441366     swim_Training             1
6        49054  47.558523 -1.035034     swim_Training             1
7        49063  47.349479 -0.772676     swim_Training             1
8        49080  47.684171 -0.495930     swim_Training             1
9        49099  47.045440 -0.877886  swim_Competition             1
10       49099  47.045440 -0.877886      swim_Leisure             1
11       49103  47.707163 -1.020701     swim_Training             1
12       49125  47.191472 -0.278336     swim_Training             1
13       49127  47.678052 -0.254608     swim_Training             1
14       49176  47.630774 -0.749882     swim_Training             1
15       49180  47.398472 -0.107579  swim_Competition             1
16       49180  47.398472 -0.107579     swim_Training             1
17       49212  47.384045 -0.868273     swim_Training             1
18       49228  47.507016  0.109707     swim_Training             1
19       49244  47.342980 -0.869187     swim_Training             1
20       49259  47.350837 -0.650474     swim_Training             2
21       49261  47.374115 -0.222563     swim_Training             1
22       49267  47.473811 -0.485526     swim_Training             2
23       49277  47.666093 -0.895242     swim_Training             1
24       49328  47.267385 -0.083041     swim_Training             4
25       49353  47.451357 -0.473459     swim_Training             1
26       49367  47.588220 -0.849651  swim_Competition             1

In [22]:
# ALL SPORTS : CLUSTERING PREPARATION - REVIEWING COLUMNS
# pre_clustering_44_foot.columns
# GIVES : Index(['Code_INSEE', 'lat', 'long', 'Niveau_activite', 'Nombre_equipements'], dtype='object')
# pre_clustering_44_basket.columns
# GIVES : Index(['Code_INSEE', 'lat', 'long', 'Niveau_activite', 'Nombre_equipements'], dtype='object')
pre_clustering_44_swim.columns
# GIVES : Index(['Code_INSEE', 'lat', 'long', 'Niveau_activite', 'Nombre_equipements'], dtype='object')

Index(['Code_INSEE', 'lat', 'long', 'Niveau_activite', 'Nombre_equipements'], dtype='object')

In [105]:
# ALL SPORTS : CLUSTERING PREPARATION - JOINING DATAS

# NO grouped_clustering_49=grouped_clustering_49_foot["Code_INSEE","lat","long","Niveau_activite"]

#for join values convert values to string
#grouped_clustering_49_foot['Nombre_equipements'] = grouped_clustering_49_foot['Nombre_equipements'].astype(str)
#create mapping dict by dict comprehension
#L = ['1','2']
#d = {x: ','.join(L) for x in L}
#print (d)
#{'2': '1,2', '1': '1,2'}

#replace values by dict
#grouped_clustering_49_foot_2 = grouped_clustering_49_foot['SUB_NUM'].replace(d)



#grouped_clustering_49.join (grouped_clustering_49_basket.set_index( [ 'Code_INSEE',"lat","long","Niveau_activite" ] ), on=[ 'Code_INSEE',"lat","long","Niveau_activite" ], how='left' , lsuffix='_left', rsuffix='_right')
# grouped_clustering_49.join (grouped_clustering_49_swim.set_index( [ 'Code_INSEE',"lat","long","Niveau_activite" ] ), on=[ 'Code_INSEE',"lat","long","Niveau_activite" ], how='left' , lsuffix='_left', rsuffix='_right')

frames = [grouped_clustering_49_foot, grouped_clustering_49_basket, grouped_clustering_49_swim]
grouped_clustering_49 = pd.concat(frames)
grouped_clustering_49


#pre_clustering_49.shape


Code_INSEE        lat      long   Niveau_activite  sum_nb_equip
0        49001  47.314889 -0.416673  foot_Competition             1
1        49001  47.314889 -0.416673     foot_Training             1
2        49002  47.303475  0.011113  foot_Competition             4
3        49003  47.257383 -0.337428  foot_Competition             2
4        49003  47.257383 -0.337428      foot_Leisure             1
..         ...        ...       ...               ...           ...
22       49267  47.473811 -0.485526     swim_Training             2
23       49277  47.666093 -0.895242     swim_Training             1
24       49328  47.267385 -0.083041     swim_Training             4
25       49353  47.451357 -0.473459     swim_Training             1
26       49367  47.588220 -0.849651  swim_Competition             1

[1077 rows x 5 columns]

In [106]:
grouped_clustering_49["Niveau_activite_NEW"] = grouped_clustering_49["Niveau_activite"] + '_' + grouped_clustering_49["sum_nb_equip"].apply(str)
del grouped_clustering_49["Niveau_activite"]
del grouped_clustering_49["sum_nb_equip"]
grouped_clustering_49

Code_INSEE        lat      long Niveau_activite_NEW
0        49001  47.314889 -0.416673  foot_Competition_1
1        49001  47.314889 -0.416673     foot_Training_1
2        49002  47.303475  0.011113  foot_Competition_4
3        49003  47.257383 -0.337428  foot_Competition_2
4        49003  47.257383 -0.337428      foot_Leisure_1
..         ...        ...       ...                 ...
22       49267  47.473811 -0.485526     swim_Training_2
23       49277  47.666093 -0.895242     swim_Training_1
24       49328  47.267385 -0.083041     swim_Training_4
25       49353  47.451357 -0.473459     swim_Training_1
26       49367  47.588220 -0.849651  swim_Competition_1

[1077 rows x 4 columns]

In [107]:
# one hot encoding
clustering_49_onehot = pd.get_dummies(grouped_clustering_49[['Niveau_activite_NEW']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
clustering_49_onehot['Code_INSEE'] = grouped_clustering_49['Code_INSEE'] 

# move neighborhood column to the first column
fixed_columns = [clustering_49_onehot.columns[-1]] + list(clustering_49_onehot.columns[:-1])
clustering_49_onehot = clustering_49_onehot[fixed_columns]

clustering_49_onehot.head()

Code_INSEE  Non defini_1  Non defini_2  Scolaire_1  Scolaire_10  \
0       49001             0             0           0            0   
1       49001             0             0           0            0   
2       49002             0             0           0            0   
3       49003             0             0           0            0   
4       49003             0             0           0            0   

   Scolaire_11  Scolaire_13  Scolaire_14  Scolaire_2  Scolaire_21  ...  \
0            0            0            0           0            0  ...   
1            0            0            0           0            0  ...   
2            0            0            0           0            0  ...   
3            0            0            0           0            0  ...   
4            0            0            0           0            0  ...   

   foot_Training_13  foot_Training_2  foot_Training_3  foot_Training_4  \
0                 0                0                0                0   
1                 0                0                0                0   
2                 0                0                0                0   
3                 0                0                0                0   
4                 0                0                0                0   

   foot_Training_7  swim_Competition_1  swim_Leisure_1  swim_Training_1  \
0                0                   0               0                0   
1                0                   0               0                0   
2                0                   0               0                0   
3                0                   0               0                0   
4                0                   0               0                0   

   swim_Training_2  swim_Training_4  
0                0                0  
1                0                0  
2                0                0  
3                0                0  
4                0                0  

[5 rows x 74 columns]

In [108]:
clustering_49_onehot.shape

(1077, 74)

In [109]:
clustering_49_grouped = clustering_49_onehot.groupby('Code_INSEE').mean().reset_index()
clustering_49_grouped

Code_INSEE  Non defini_1  Non defini_2  Scolaire_1  Scolaire_10  \
0         49001           0.0           0.0    0.000000          0.0   
1         49002           0.0           0.0    0.000000          0.0   
2         49003           0.0           0.0    0.000000          0.0   
3         49004           0.0           0.0    0.000000          0.0   
4         49005           0.0           0.0    0.000000          0.0   
..          ...           ...           ...         ...          ...   
280       49375           0.0           0.0    0.000000          0.0   
281       49376           0.0           0.0    0.333333          0.0   
282       49377           0.0           0.0    0.000000          0.0   
283       49378           0.0           0.0    0.500000          0.0   
284       49381           0.0           0.0    0.000000          0.0   

     Scolaire_11  Scolaire_13  Scolaire_14  Scolaire_2  Scolaire_21  ...  \
0            0.0          0.0          0.0         0.0          0.0  ...   
1            0.0          0.0          0.0         0.0          0.0  ...   
2            0.0          0.0          0.0         0.0          0.0  ...   
3            0.0          0.0          0.0         0.0          0.0  ...   
4            0.0          0.0          0.0         0.0          0.0  ...   
..           ...          ...          ...         ...          ...  ...   
280          0.0          0.0          0.0         0.0          0.0  ...   
281          0.0          0.0          0.0         0.0          0.0  ...   
282          0.0          0.0          0.0         0.0          0.0  ...   
283          0.0          0.0          0.0         0.0          0.0  ...   
284          0.0          0.0          0.0         0.0          0.0  ...   

     foot_Training_13  foot_Training_2  foot_Training_3  foot_Training_4  \
0                 0.0              0.0              0.0              0.0   
1                 0.0              0.0              0.0              0.0   
2                 0.0              0.0              0.0              0.0   
3                 0.0              0.0              0.0              0.0   
4                 0.0              0.0              0.0              0.0   
..                ...              ...              ...              ...   
280               0.0              0.0              0.0              0.0   
281               0.0              0.0              0.0              0.0   
282               0.0              0.0              0.0              0.0   
283               0.0              0.0              0.0              0.0   
284               0.0              0.0              0.0              0.0   

     foot_Training_7  swim_Competition_1  swim_Leisure_1  swim_Training_1  \
0                0.0                 0.0             0.0              0.0   
1                0.0                 0.0             0.0              0.0   
2                0.0                 0.0             0.0              0.0   
3                0.0                 0.0             0.0              0.0   
4                0.0                 0.0             0.0              0.0   
..               ...                 ...             ...              ...   
280              0.0                 0.0             0.0              0.0   
281              0.0                 0.0             0.0              0.0   
282              0.0                 0.0             0.0              0.0   
283              0.0                 0.0             0.0              0.0   
284              0.0                 0.0             0.0              0.0   

     swim_Training_2  swim_Training_4  
0                0.0              0.0  
1                0.0              0.0  
2                0.0              0.0  
3                0.0              0.0  
4                0.0              0.0  
..               ...              ...  
280              0.0              0.0  
281              0.0              0.0  
282              0.0         

In [110]:
# Let's confirm the new size :
clustering_49_grouped['Code_INSEE']=clustering_49_grouped['Code_INSEE'].apply(str)
clustering_49_grouped.shape


(285, 74)

In [111]:
# Let's print each district along with the top 5 most common equipements
num_top_sp_equip = 5

for hood in clustering_49_grouped['Code_INSEE']:
    print("----"+hood+"----")
    temp = clustering_49_grouped[clustering_49_grouped['Code_INSEE'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_sp_equip))
    print('\n')

----49001----
                venue  freq
0  foot_Competition_1   0.5
1     foot_Training_1   0.5
2      foot_Leisure_3   0.0
3     foot_Leisure_15   0.0
4     foot_Leisure_13   0.0


----49002----
                  venue  freq
0  basket_Competition_1   0.5
1    foot_Competition_4   0.5
2    foot_Competition_8   0.0
3        foot_Leisure_2   0.0
4       foot_Leisure_15   0.0


----49003----
                venue  freq
0  foot_Competition_2  0.33
1      foot_Leisure_1  0.33
2    basket_Leisure_1  0.33
3        Non defini_1  0.00
4  foot_Competition_8  0.00


----49004----
                 venue  freq
0   foot_Competition_1  0.33
1       foot_Leisure_3  0.33
2     basket_Leisure_2  0.33
3   foot_Competition_2  0.00
4  foot_Competition_25  0.00


----49005----
                 venue  freq
0       foot_Leisure_1   1.0
1         Non defini_1   0.0
2  foot_Competition_10   0.0
3       foot_Leisure_2   0.0
4      foot_Leisure_15   0.0


----49006----
                  venue  freq
0  basket_Co

4     foot_Leisure_15  0.00


----49082----
                venue  freq
0  foot_Competition_2   1.0
1        Non defini_1   0.0
2  foot_Competition_8   0.0
3      foot_Leisure_2   0.0
4     foot_Leisure_15   0.0


----49083----
                  venue  freq
0  basket_Competition_1  0.33
1    foot_Competition_3  0.33
2        foot_Leisure_1  0.33
3    foot_Competition_8  0.00
4        foot_Leisure_2  0.00


----49085----
                venue  freq
0  foot_Competition_2   1.0
1        Non defini_1   0.0
2  foot_Competition_8   0.0
3      foot_Leisure_2   0.0
4     foot_Leisure_15   0.0


----49086----
                  venue  freq
0  basket_Competition_1   0.5
1    foot_Competition_3   0.5
2    foot_Competition_8   0.0
3        foot_Leisure_2   0.0
4       foot_Leisure_15   0.0


----49088----
                venue  freq
0  foot_Competition_1  0.33
1          Scolaire_1  0.33
2     foot_Training_1  0.33
3  foot_Competition_7  0.00
4     foot_Leisure_15  0.00


----49089----
            

                  venue  freq
0  basket_Competition_1   0.5
1    foot_Competition_2   0.5
2    foot_Competition_8   0.0
3        foot_Leisure_2   0.0
4       foot_Leisure_15   0.0


----49167----
                  venue  freq
0  basket_Competition_1  0.14
1      basket_Leisure_2  0.14
2            Scolaire_1  0.14
3        foot_Leisure_3  0.14
4    foot_Competition_5  0.14


----49169----
                  venue  freq
0            Scolaire_1   0.2
1    foot_Competition_2   0.2
2        foot_Leisure_2   0.2
3            Scolaire_2   0.2
4  basket_Competition_1   0.2


----49170----
                 venue  freq
0           Scolaire_1   0.4
1   foot_Competition_1   0.2
2     basket_Leisure_1   0.2
3       foot_Leisure_3   0.2
4  foot_Competition_25   0.0


----49172----
                venue  freq
0  foot_Competition_1  0.25
1    basket_Leisure_1  0.25
2     foot_Training_2  0.25
3      foot_Leisure_2  0.25
4  foot_Competition_2  0.00


----49174----
                  venue  freq
0  baske

              venue  freq
0    foot_Leisure_2   0.5
1  basket_Leisure_1   0.5
2    foot_Leisure_3   0.0
3   foot_Leisure_15   0.0
4   foot_Leisure_13   0.0


----49252----
              venue  freq
0    foot_Leisure_1   0.5
1  basket_Leisure_1   0.5
2      Non defini_1   0.0
3    foot_Leisure_3   0.0
4   foot_Leisure_15   0.0


----49253----
                  venue  freq
0        foot_Leisure_4  0.25
1    foot_Competition_3  0.25
2      basket_Leisure_2  0.25
3  basket_Competition_1  0.25
4   foot_Competition_25  0.00


----49254----
                 venue  freq
0   foot_Competition_1   1.0
1  foot_Competition_10   0.0
2       foot_Leisure_2   0.0
3      foot_Leisure_15   0.0
4      foot_Leisure_13   0.0


----49256----
                venue  freq
0          Scolaire_1  0.67
1      foot_Leisure_1  0.33
2        Non defini_1  0.00
3  foot_Competition_7  0.00
4      foot_Leisure_2  0.00


----49257----
                venue  freq
0  foot_Competition_1   0.5
1     foot_Training_1   0.5
2 

                 venue  freq
0   foot_Competition_1   1.0
1  foot_Competition_10   0.0
2       foot_Leisure_2   0.0
3      foot_Leisure_15   0.0
4      foot_Leisure_13   0.0


----49316----
                  venue  freq
0  basket_Competition_1   0.5
1    foot_Competition_2   0.5
2    foot_Competition_8   0.0
3        foot_Leisure_2   0.0
4       foot_Leisure_15   0.0


----49317----
                  venue  freq
0    foot_Competition_1  0.33
1        foot_Leisure_1  0.33
2  basket_Competition_1  0.33
3    foot_Competition_2  0.00
4   foot_Competition_25  0.00


----49318----
                  venue  freq
0            Scolaire_1  0.50
1  basket_Competition_1  0.25
2    foot_Competition_2  0.25
3    foot_Competition_9  0.00
4        foot_Leisure_3  0.00


----49321----
                 venue  freq
0       foot_Leisure_1   1.0
1         Non defini_1   0.0
2  foot_Competition_10   0.0
3       foot_Leisure_2   0.0
4      foot_Leisure_15   0.0


----49323----
                venue  freq
0  f

In [112]:
def return_most_common_equip(row, num_top_sp_equip):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_sp_equip]

In [113]:
num_top_equip = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top equip
columns = ['Code_INSEE']
for ind in np.arange(num_top_equip):
    try:
        columns.append('{}{} Most Common Equip'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Equip'.format(ind+1))

# create a new dataframe
neighborhoods_equip_sorted = pd.DataFrame(columns=columns)
neighborhoods_equip_sorted['Code_INSEE'] = clustering_49_grouped['Code_INSEE']

for ind in np.arange(clustering_49_grouped.shape[0]):
    neighborhoods_equip_sorted.iloc[ind, 1:] = return_most_common_equip(clustering_49_grouped.iloc[ind, :], num_top_equip)

neighborhoods_equip_sorted.head()

Code_INSEE 1st Most Common Equip 2nd Most Common Equip  \
0      49001    foot_Competition_1       foot_Training_1   
1      49002  basket_Competition_1    foot_Competition_4   
2      49003      basket_Leisure_1        foot_Leisure_1   
3      49004    foot_Competition_1      basket_Leisure_2   
4      49005        foot_Leisure_1       swim_Training_4   

  3rd Most Common Equip 4th Most Common Equip 5th Most Common Equip  \
0           Scolaire_96  basket_Competition_1  basket_Competition_2   
1       swim_Training_4      basket_Leisure_1  basket_Competition_2   
2    foot_Competition_2  basket_Competition_8  basket_Competition_1   
3        foot_Leisure_3            Scolaire_1      basket_Leisure_1   
4            Scolaire_9  basket_Competition_1  basket_Competition_2   

  6th Most Common Equip 7th Most Common Equip 8th Most Common Equip  \
0  basket_Competition_3  basket_Competition_4  basket_Competition_5   
1  basket_Competition_3  basket_Competition_4  basket_Competition_5   
2  basket_Competition_2  basket_Competition_3  basket_Competition_4   
3  basket_Competition_1  basket_Competition_2  basket_Competition_3   
4  basket_Competition_3  basket_Competition_4  basket_Competition_5   

  9th Most Common Equip 10th Most Common Equip  
0  basket_Competition_8       basket_Leisure_1  
1  basket_Competition_8      basket_Leisure_19  
2  basket_Competition_5        swim_Training_4  
3  basket_Competition_4   basket_Competition_5  
4  basket_Competition_8       basket_Leisure_1

In [116]:
# set number of clusters
kclusters = 5

clustering_49_grouped_clustering = clustering_49_grouped.drop('Code_INSEE', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(clustering_49_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([1, 2, 4, 2, 0, 2, 2, 3, 1, 2])

In [117]:
# add clustering labels
#one time only : 
neighborhoods_equip_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

clustering_49_merged = myCP

# merge clustering_49_grouped with clustering_49_data to add latitude/longitude for each district
clustering_49_merged['Code_INSEE']=clustering_49_merged['Code_INSEE'].astype(int)
neighborhoods_equip_sorted['Code_INSEE']=neighborhoods_equip_sorted['Code_INSEE'].astype(int)
clustering_49_merged = clustering_49_merged.merge(neighborhoods_equip_sorted.set_index('Code_INSEE'), on='Code_INSEE')

clustering_49_merged.head() # check the last columns!

Code_INSEE  Nom_commune        lat      long  Cluster Labels  \
0       49007       ANGERS  47.476837 -0.556126               2   
1       49015      AVRILLE  47.505711 -0.600789               2   
2       49020    BEAUCOUZE  47.474451 -0.634055               2   
3       49035  BOUCHEMAINE  47.430767 -0.627122               2   
4       49048     BRIOLLAY  47.576398 -0.497931               2   

  1st Most Common Equip 2nd Most Common Equip 3rd Most Common Equip  \
0          Non defini_1     basket_Leisure_19  basket_Competition_1   
1      basket_Leisure_5   foot_Competition_12  basket_Competition_4   
2       foot_Training_1      basket_Leisure_2        foot_Leisure_4   
3          Non defini_1    foot_Competition_4  basket_Competition_1   
4            Scolaire_2    foot_Competition_4  basket_Competition_1   

  4th Most Common Equip 5th Most Common Equip 6th Most Common Equip  \
0           Scolaire_53       foot_Leisure_53    foot_Competition_4   
1       foot_Leisure_13           Scolaire_13       foot_Training_1   
2  basket_Competition_2    foot_Competition_6            Scolaire_3   
3        foot_Leisure_6       foot_Training_1      basket_Leisure_3   
4        foot_Leisure_2      basket_Leisure_1  basket_Competition_8   

  7th Most Common Equip 8th Most Common Equip 9th Most Common Equip  \
0           Scolaire_96       foot_Training_7            Scolaire_1   
1    swim_Competition_1            Scolaire_9     basket_Leisure_28   
2            Scolaire_8     basket_Leisure_19      basket_Leisure_1   
3     basket_Leisure_28      basket_Leisure_2     basket_Leisure_19   
4           Scolaire_96  basket_Competition_2  basket_Competition_3   

  10th Most Common Equip  
0           Non defini_2  
1       basket_Leisure_2  
2   basket_Competition_8  
3       basket_Leisure_1  
4   basket_Competition_4

In [121]:
# create map
map_clusters = folium.Map(location=[47.478419, -0.563166], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(clustering_49_merged['lat'], clustering_49_merged['long'], clustering_49_merged['Code_INSEE'], clustering_49_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

In [134]:
# Examine Clusters :
# "basket ready" districts
clustering_49_merged.loc[clustering_49_merged['Cluster Labels'] == 0, clustering_49_merged.columns[[1] + list(range(5, clustering_49_merged.shape[1]))]]

Empty DataFrame
Columns: [Nom_commune, 1st Most Common Equip, 2nd Most Common Equip, 3rd Most Common Equip, 4th Most Common Equip, 5th Most Common Equip, 6th Most Common Equip, 7th Most Common Equip, 8th Most Common Equip, 9th Most Common Equip, 10th Most Common Equip]
Index: []

In [135]:
# Examine Clusters :
# rather "leisure only" district
clustering_49_merged.loc[clustering_49_merged['Cluster Labels'] == 1, clustering_49_merged.columns[[1] + list(range(5, clustering_49_merged.shape[1]))]]

Empty DataFrame
Columns: [Nom_commune, 1st Most Common Equip, 2nd Most Common Equip, 3rd Most Common Equip, 4th Most Common Equip, 5th Most Common Equip, 6th Most Common Equip, 7th Most Common Equip, 8th Most Common Equip, 9th Most Common Equip, 10th Most Common Equip]
Index: []

In [129]:
# Examine Clusters :
# Center : " Highly Equiped " 
clustering_49_merged.loc[clustering_49_merged['Cluster Labels'] == 2, clustering_49_merged.columns[[1] + list(range(5, clustering_49_merged.shape[1]))]]

Nom_commune 1st Most Common Equip 2nd Most Common Equip  \
0                   ANGERS          Non defini_1     basket_Leisure_19   
1                  AVRILLE      basket_Leisure_5   foot_Competition_12   
2                BEAUCOUZE       foot_Training_1      basket_Leisure_2   
3              BOUCHEMAINE          Non defini_1    foot_Competition_4   
4                 BRIOLLAY            Scolaire_2    foot_Competition_4   
5         CANTENAY EPINARD       foot_Training_1  basket_Competition_1   
6                ECOUFLANT        foot_Leisure_2            Scolaire_2   
8                    FENEU  basket_Competition_1      basket_Leisure_2   
9            LOIRE AUTHION      basket_Leisure_1  basket_Competition_1   
10      LONGUENEE EN ANJOU        foot_Leisure_3  basket_Competition_1   
11    LE PLESSIS GRAMMOIRE        foot_Leisure_2            Scolaire_2   
12         LES PONTS DE CE           Scolaire_21        foot_Leisure_7   
13        MONTREUIL JUIGNE            Scolaire_7      basket_Leisure_2   
15  RIVES DU LOIR EN ANJOU       foot_Training_1  basket_Competition_1   
17             SAVENNIERES    foot_Competition_1        foot_Leisure_2   
20   ST BARTHELEMY D ANJOU     basket_Training_1    foot_Competition_7   
22  ST LAMBERT LA POTHERIE    foot_Competition_4  basket_Competition_1   
23    ST LEGER DE LINIERES      basket_Leisure_1  basket_Competition_1   
24  ST MARTIN DU FOUILLOUX        foot_Leisure_4  basket_Competition_1   
25    STE GEMMES SUR LOIRE            Scolaire_3            Scolaire_1   
26                 TRELAZE       foot_Training_1            Scolaire_3   
27      VERRIERES EN ANJOU     basket_Training_2       foot_Training_2   

   3rd Most Common Equip 4th Most Common Equip 5th Most Common Equip  \
0   basket_Competition_1           Scolaire_53       foot_Leisure_53   
1   basket_Competition_4       foot_Leisure_13           Scolaire_13   
2         foot_Leisure_4  basket_Competition_2    foot_Competition_6   
3   basket_Competition_1        foot_Leisure_6       foot_Training_1   
4   basket_Competition_1        foot_Leisure_2      basket_Leisure_1   
5     foot_Competition_3       swim_Training_4           Scolaire_96   
6   basket_Competition_1    foot_Competition_5            Scolaire_3   
8     foot_Competition_4        foot_Leisure_2       swim_Training_4   
9     foot_Competition_3        foot_Leisure_2  basket_Competition_8   
10      basket_Leisure_2    foot_Competition_4  basket_Competition_8   
11  basket_Competition_1    foot_Competition_4      basket_Leisure_1   
12     basket_Training_1    foot_Competition_9           Scolaire_10   
13  basket_Competition_2        foot_Leisure_5    foot_Competition_8   
15    foot_Competition_3       swim_Training_4           Scolaire_96   
17      basket_Leisure_1      basket_Leisure_5      basket_Leisure_4   
20       foot_Leisure_15      basket_Leisure_9  basket_Competition_2   
22        foot_Leisure_1            Scolaire_2      basket_Leisure_1   
23    foot_Competition_4        foot_Leisure_2  basket_Competition_8   
24      basket_Leisure_2    foot_Competition_3       swim_Training_4   
25  basket_Competition_2        foot_Leisure_5    foot_Competition_9   
26       swim_Training_1      basket_Leisure_4            Scolaire_1   
27        foot_Leisure_3  basket_Competition_1            Scolaire_4   

   6th Most Common Equip 7th Most Common Equip 8th Most Common Equip  \
0     foot_Competition_4           Scolaire_96       foot_Training_7   
1        foot_Training_1    swim_Competition_1            Scolaire_9   
2             Scolaire_3            Scolaire_8     basket_Leisure_19   
3       basket_Leisure_3     basket_Leisure_28      basket_Leisure_2   
4   basket_Competition_8           Scolaire_96  basket_Competition_2   
5   basket_Competition_2  basket_Competition_3  basket_Competition_4   
6       basket_Leisure_1       foot_Training_1     basket_Leisure_19   
8   basket_Competition_5           Scolaire_96  basket_Competition_2   
9      

In [132]:
# Examine Clusters :
# 
clustering_49_merged.loc[clustering_49_merged['Cluster Labels'] == 3, clustering_49_merged.columns[[1] + list(range(5, clustering_49_merged.shape[1]))]]

Nom_commune 1st Most Common Equip 2nd Most Common Equip  \
7                  ECUILLE            Scolaire_1        foot_Leisure_2   
14             MURS ERIGNE            Scolaire_1        foot_Leisure_3   
16                SARRIGNE    foot_Competition_1            Scolaire_1   
18   SOULAINES SUR AUBANCE            Scolaire_1        foot_Leisure_5   
21  ST CLEMENT DE LA PLACE            Scolaire_1       foot_Training_1   

   3rd Most Common Equip 4th Most Common Equip 5th Most Common Equip  \
7       basket_Leisure_1       swim_Training_4  basket_Competition_8   
14  basket_Competition_2    foot_Competition_7       foot_Training_2   
16            Scolaire_2      basket_Leisure_1  basket_Competition_1   
18      basket_Leisure_3       swim_Training_4  basket_Competition_8   
21      basket_Leisure_1  basket_Competition_1        foot_Leisure_1   

   6th Most Common Equip 7th Most Common Equip 8th Most Common Equip  \
7            Scolaire_96  basket_Competition_1  basket_Competition_2   
14       swim_Training_4  basket_Competition_8  basket_Competition_1   
16  basket_Competition_2  basket_Competition_3  basket_Competition_4   
18  basket_Competition_1  basket_Competition_2  basket_Competition_3   
21    foot_Competition_2  basket_Competition_2  basket_Competition_3   

   9th Most Common Equip 10th Most Common Equip  
7   basket_Competition_3   basket_Competition_4  
14  basket_Competition_3   basket_Competition_4  
16  basket_Competition_5   basket_Competition_8  
18  basket_Competition_4   basket_Competition_5  
21  basket_Competition_4   basket_Competition_5

In [133]:
# Examine Clusters :
# 
clustering_49_merged.loc[clustering_49_merged['Cluster Labels'] == 4, clustering_49_merged.columns[[1] + list(range(5, clustering_49_merged.shape[1]))]]

Nom_commune 1st Most Common Equip 2nd Most Common Equip  \
19  SOULAIRE ET BOURG      basket_Leisure_1       foot_Training_1   

   3rd Most Common Equip 4th Most Common Equip 5th Most Common Equip  \
19  basket_Competition_1        foot_Leisure_1    foot_Competition_2   

   6th Most Common Equip 7th Most Common Equip 8th Most Common Equip  \
19  basket_Competition_2  basket_Competition_3  basket_Competition_4   

   9th Most Common Equip 10th Most Common Equip  
19  basket_Competition_5   basket_Competition_8

In [79]:
# add new datas about populations by districts
myDEMOG=pd.read_csv('communes49_CL1.csv',delimiter=';')
# myDEMOG.shape
# (22, 3)
myDEMOG

Code_INSEE        Nom_de_la_commune  Population_totale
0        49007                   ANGERS             157577
1        49015                  AVRILLE              14420
2        49020                BEAUCOUZE               5402
3        49035              BOUCHEMAINE               6937
4        49048                 BRIOLLAY               3076
5        49055         CANTENAY EPINARD               2352
6        49129                ECOUFLANT               4305
7        49135                    FENEU               2209
8        49241     LE PLESSIS GRAMMOIRE               2508
9        49246          LES PONTS DE CE              13354
10       49307           LOIRE AUTHION               16394
11       49200       LONGUENEE EN ANJOU               6483
12       49214         MONTREUIL JUIGNE               7669
13       49377  RIVES DU LOIR EN ANJOU                5709
14       49267    ST BARTHELEMY D ANJOU               9436
15       49294   ST LAMBERT LA POTHERIE               2910
16       49298    ST LEGER DE LINIERES                3699
17       49306   ST MARTIN DU FOUILLOUX               1710
18       49278     STE GEMMES SUR LOIRE               3649
19       49329              SAVENNIERES               1386
20       49353                  TRELAZE              14924
21       49323       VERRIERES EN ANJOU               7659

In [145]:
my_stat_level_foot2B=my_stat_level_foot2.merge(myDEMOG, left_on='Code_INSEE', right_on='Code_INSEE')
my_stat_level_foot2B['nb_equip_by_1000hab']=1000*my_stat_level_foot2B['Nombre_equipements']/my_stat_level_foot2B['Population_totale']
my_stat_level_foot2C=my_stat_level_foot2B.sort_values(by = 'nb_equip_by_1000hab', ascending = False)
df_2D_mask=my_stat_level_foot2C['nb_equip_by_1000hab']>=0.6
my_stat_level_foot2D=my_stat_level_foot2C[df_2D_mask]
my_stat_level_foot2D


Code_INSEE Niveau_activite  Nombre_equipements       Nom_de_la_commune  \
49       49278     Competition                   7    STE GEMMES SUR LOIRE   
29       49135     Competition                   3                   FENEU   
37       49241     Competition                   3    LE PLESSIS GRAMMOIRE   
58       49306         Leisure                   2  ST MARTIN DU FOUILLOUX   
57       49306     Competition                   2  ST MARTIN DU FOUILLOUX   
52       49294     Competition                   3  ST LAMBERT LA POTHERIE   
21       49048     Competition                   3                BRIOLLAY   
25       49129     Competition                   4               ECOUFLANT   
16       49020        Scolaire                   5               BEAUCOUZE   
23       49055     Competition                   2        CANTENAY EPINARD   
44       49246        Scolaire                  11         LES PONTS DE CE   
50       49278         Leisure                   3    STE GEMMES SUR LOIRE   
55       49298     Competition                   3   ST LEGER DE LINIERES    
65       49329         Leisure                   1             SAVENNIERES   
64       49329     Competition                   1             SAVENNIERES   
54       49294        Scolaire                   2  ST LAMBERT LA POTHERIE   
63       49323        Scolaire                   5      VERRIERES EN ANJOU   
47       49267         Leisure                   6   ST BARTHELEMY D ANJOU   

    Population_totale  nb_equip_by_1000hab  
49               3649             1.918334  
29               2209             1.358081  
37               2508             1.196172  
58               1710             1.169591  
57               1710             1.169591  
52               2910             1.030928  
21               3076             0.975293  
25               4305             0.929152  
16               5402             0.925583  
23               2352             0.850340  
44              13354             0.823723  
50               3649             0.822143  
55               3699             0.811030  
65               1386             0.721501  
64               1386             0.721501  
54               2910             0.687285  
63               7659             0.652827  
47               9436             0.635863

In [144]:
my_stat_level_basket2B=my_stat_level_basket2.merge(myDEMOG, left_on='Code_INSEE', right_on='Code_INSEE')
my_stat_level_basket2B['nb_equip_by_1000hab']=1000*my_stat_level_basket2B['Nombre_equipements']/my_stat_level_basket2B['Population_totale']
my_stat_level_basket2C=my_stat_level_basket2B.sort_values(by = 'nb_equip_by_1000hab', ascending = False)
df_2D_mask=my_stat_level_basket2C['nb_equip_by_1000hab']>=0.5
my_stat_level_basket2D=my_stat_level_basket2C[df_2D_mask]
my_stat_level_basket2D

Code_INSEE Niveau_activite  Nombre_equipements       Nom_de_la_commune  \
48       49306         Leisure                   2  ST MARTIN DU FOUILLOUX   
39       49267         Leisure                   9   ST BARTHELEMY D ANJOU   
22       49135         Leisure                   2                   FENEU   
35       49246        Scolaire                  10         LES PONTS DE CE   
55       49329         Leisure                   1             SAVENNIERES   
16       49048        Scolaire                   2                BRIOLLAY   
6        49015        Scolaire                   9                 AVRILLE   
47       49306     Competition                   1  ST MARTIN DU FOUILLOUX   
10       49020        Scolaire                   3               BEAUCOUZE   
41       49278     Competition                   2    STE GEMMES SUR LOIRE   
42       49278         Leisure                   2    STE GEMMES SUR LOIRE   
40       49267        Scolaire                   5   ST BARTHELEMY D ANJOU   
54       49323        Scolaire                   4      VERRIERES EN ANJOU   

    Population_totale  nb_equip_by_1000hab  
48               1710             1.169591  
39               9436             0.953794  
22               2209             0.905387  
35              13354             0.748839  
55               1386             0.721501  
16               3076             0.650195  
6               14420             0.624133  
47               1710             0.584795  
10               5402             0.555350  
41               3649             0.548095  
42               3649             0.548095  
40               9436             0.529886  
54               7659             0.522261

In [143]:
my_stat_level_swim2B=my_stat_level_swim2.merge(myDEMOG, left_on='Code_INSEE', right_on='Code_INSEE')
my_stat_level_swim2B['nb_equip_by_10000hab']=1000*my_stat_level_swim2B['Nombre_equipements']/my_stat_level_swim2B['Population_totale']
my_stat_level_swim2C=my_stat_level_swim2B.sort_values(by = 'nb_equip_by_10000hab', ascending = False)
df_2D_mask=my_stat_level_swim2C['nb_equip_by_10000hab']>=0.0000001
my_stat_level_swim2D=my_stat_level_swim2C[df_2D_mask]
my_stat_level_swim2D


Code_INSEE Niveau_activite  Nombre_equipements      Nom_de_la_commune  \
3       49267        Training                   2  ST BARTHELEMY D ANJOU   
2       49015     Competition                   1                AVRILLE   
4       49353        Training                   1                TRELAZE   
0       49007        Training                   1                 ANGERS   
1       49007        Scolaire                   1                 ANGERS   

   Population_totale  nb_equip_by_10000hab  
3               9436              0.211954  
2              14420              0.069348  
4              14924              0.067006  
0             157577              0.006346  
1             157577              0.006346